In [0]:
spark

#Establishing connection between databricks and ADLS gen2

In [0]:
## please enter the storage account name in place of <storage-account>
## please create an app registration and use the application id and directory id and paste it in place of <application-id> and <directory-id>
## please create a secret key in app registration and then use the key in place of service_credential
## in the storage account go to IAM and add role Contributor for the app registration.

spark.conf.set("fs.azure.account.auth.type.<storage-account>.dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type.<storage-account>.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set("fs.azure.account.oauth2.client.id.<storage-account>.dfs.core.windows.net", "<application-id>")
spark.conf.set("fs.azure.account.oauth2.client.secret.<storage-account>.dfs.core.windows.net", service_credential)
spark.conf.set("fs.azure.account.oauth2.client.endpoint.<storage-account>.dfs.core.windows.net", "https://login.microsoftonline.com/<directory-id>/oauth2/token")



In [0]:
# customers_df=spark.read.format('csv').option("header","true").option("inferschema","true").load("abfss://olist-container@ecommprojstorage.dfs.core.windows.net/bronze/olist_customers_dataset.csv")
# display(customers_df)

#reading data from adls gen2


In [0]:
base_path="abfss://olist-container@ecommprojstorage.dfs.core.windows.net/bronze/"
customers_path=base_path+"olist_customers_dataset.csv"
geolocation_path=base_path+"olist_geolocation_dataset.csv"
order_items_path=base_path+"olist_order_items_dataset.csv"
order_payments_path=base_path+"olist_order_payments_dataset.csv"
order_review_path=base_path+"olist_order_reviews_dataset.csv"
orders_path=base_path+"olist_orders_dataset.csv"
products_path=base_path+"olist_products_dataset.csv"
sellers_path=base_path+"olist_sellers_dataset.csv"


In [0]:
customers_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(customers_path)
geolocation_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(geolocation_path)
order_items_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(order_items_path)
order_payments_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(order_payments_path)
order_review_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(order_review_path)
orders_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(orders_path)
products_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(products_path)
sellers_df=spark.read.format('csv').option('header','true').option('inferschema','true').load(sellers_path)

#Establishing connection from mongodb to get the data and store it as pandas DF

In [0]:
import pymongo

In [0]:
from pymongo import MongoClient

In [0]:
# importing module
from pymongo import MongoClient

hostname = "a-52ie.h.filess.io"
database = "olistmongodb_raisethan"
port = "27018"
username = "olistmongodb_raisethan"
password = "90e0683c984be4df2cf3aa70bbfeae3a61745de5"

uri = "mongodb://" + username + ":" + password + "@" + hostname + ":" + port + "/" + database

# Connect with the portnumber and host
client = MongoClient(uri)

# Access database
mydatabase = client[database]
mydatabase

Database(MongoClient(host=['a-52ie.h.filess.io:27018'], document_class=dict, tz_aware=False, connect=True), 'olistmongodb_raisethan')

In [0]:
display(products_df)

In [0]:
import pandas as pd
collections=mydatabase["product_category_name_translation"]

mongodata=pd.DataFrame(list(collections.find())) # turned into a panda dataframe
mongodata = mongodata.drop(columns=["_id"])
#changing into spark df
mongodata_spark=spark.createDataFrame(mongodata)

In [0]:
mongodata

## Cleaning the data

In [0]:
from pyspark.sql.functions import *

def clean_data(df,name):
    print(f"cleaning data for {name}")
    return df.dropDuplicates().dropna('all')

In [0]:
orders_df_clean=clean_data(orders_df,'orders')
display(orders_df_clean)

In [0]:
#converting date columns
orders_df_clean_date=orders_df_clean.withColumn("order_purchase_timestamp",to_date("order_purchase_timestamp")\
                                                ).withColumn("order_approved_at",to_date("order_approved_at")\
                                                ).withColumn("order_delivered_carrier_date",to_date("order_delivered_carrier_date")\
                                                ).withColumn("order_delivered_customer_date",to_date("order_delivered_customer_date")\
                                                ).withColumn("order_estimated_delivery_date",to_date("order_estimated_delivery_date"))

In [0]:
# calculating the delivery and time delay.
orders_df=orders_df_clean_date.withColumn("actual_delivery_time",datediff("order_delivered_customer_date","order_purchase_timestamp"))
orders_df=orders_df.withColumn("estimated_delivery_time",datediff("order_estimated_delivery_date","order_purchase_timestamp"))
orders_df=orders_df.withColumn("delay_time",(orders_df.estimated_delivery_time - orders_df.actual_delivery_time))
display(orders_df)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date actual_delivery_time estimated_delivery_time delay_time 82daed31f80350ce51f518369a8d181c d1240cdcdb9e6f08aa9a329bf1751c0e delivered 2017-06-27 2017-06-27 2017-06-27 2017-06-29 2017-07-10 2 13 11 8adafb3466daa5395694d3a906ff9d40 b7919647bde69acc948baa47823d6c75 delivered 2017-01-25 2017-01-25 2017-02-07 2017-02-14 2017-03-23 20 57 37 4380bb6c7d8375926bbea2c8b514dc8c 11617a4c5fc72fccb4c2a53ea21c5a3c delivered 2018-01-29 2018-01-29 2018-01-31 2018-02-14 2018-02-21 16 23 7 88c588c116fd06fb8e48dd83af88ec4a 8787c72a20002592238d7b80721ab729 delivered 2017-11-19 2017-11-19 2017-11-24 2017-12-22 2017-12-12 33 23 -10 2d816b6a11ddd3843f307d1333321091 95303e4c9c23d67877e4b20afb04bfa8 delivered 2017-08-22 2017-08-22 2017-08-24 2017-08-25 2017-09-06 3 15 12 0cb25b24a27e27dd18273360995e99f4 b03b8bf457533ef245fd5fa2681732d0 delivered 2018-07-23 2018-07-23 2018-07-24 2018-07-25 2018-08-02 2 10 8 70462ebcf26934be8bd0327d2e6103d3 fb8b8298c590af3ee3169596c5ec2114 delivered 2018-08-20 2018-08-20 2018-08-21 2018-08-22 2018-08-28 2 8 6 4e21387c48145e5e07a1d552b1a69776 766a6dd9d0045e8462f001462976ff99 delivered 2018-02-06 2018-02-06 2018-02-07 2018-02-14 2018-03-02 8 24 16 ff8780cfb4535054cc5b56046b170cc0 f9835897d532524a6e9686847d4db4a7 delivered 2017-09-21 2017-09-22 2017-09-22 2017-10-01 2017-10-18 10 27 17 21094f6fd8017c8b7339040142abea71 faee0cb7b3e2c9fd9f57ec04cb70d51a delivered 2018-07-24 2018-07-24 2018-07-30 2018-08-03 2018-08-24 10 31 21 7263a9488004df94487b7f970be3b91e b7aba705e32253c6d5159e0155ba4fac delivered 2018-06-10 2018-06-11 2018-06-13 2018-06-21 2018-07-05 11 25 14 ddcb9f924091ed9cc49b9c78d37d48b6 c7093c34ad7da76feb1fb87e5f6b366b delivered 2017-04-17 2017-04-17 2017-04-18 2017-05-02 2017-05-16 15 29 14 e2ecc8a06aa292e6cf6f88f2826dd141 cac877e3b4e0495e13b2ad7c96aa5c11 delivered 2017-09-23 2017-09-23 2017-09-25 2017-09-29 2017-10-11 6 18 12 58ecdd5dee96d19e30c67a29cae63e4d d0eca4dcf131a1a0f4665c2a47b4ca02 delivered 2017-08-08 2017-08-10 2017-08-11 2017-08-24 2017-08-30 16 22 6 c95fb74948e8db073f6114d3fa726fe1 5427db81b6127984b9d282e9e6ef2603 delivered 2017-11-05 2017-11-05 2017-11-06 2017-11-22 2017-11-28 17 23 6 7b2e128ff26556462b7d217f1b67600b f57d3db30585e5fe7bb1649ec4b1bc32 delivered 2017-10-27 2017-10-27 2017-10-31 2017-11-22 2017-11-17 26 21 -5 6a2e09d7d2755c778b119d0b74d4d431 6eb6e7b6a901ac22a2e5949e1f3151e8 delivered 2018-02-23 2018-02-23 2018-02-27 2018-03-08 2018-03-16 13 21 8 a7126b0cb60c6a688dfdac0b29f66f4c c41a39d44789dfa58ded86a11abfc320 delivered 2017-07-16 2017-07-17 2017-07-18 2017-08-18 2017-08-18 33 33 0 9e22fb4a47d29059ef9689ca8b26d8b3 dc7dc47999d1b3c4c2f6a085a1a76eef delivered 2018-02-17 2018-02-17 2018-02-19 2018-03-12 2018-03-19 23 30 7 2bd2198690a2c150fe5fdc4e064ba521 01288d72df4b2a4fb61182da4113ceab delivered 2018-02-18 2018-02-18 2018-02-20 2018-03-20 2018-03-19 30 29 -1 32032cfe80a0e36537d611ea2b9342e0 1400d3c9230622c965679dc35bf3d886 delivered 2018-04-30 2018-05-01 2018-05-02 2018-05-07 2018-05-22 7 22 15 b60b122b336eaee3323565272f117bec 00146ad30454993879adaa91c518f68c delivered 2018-01-08 2018-01-08 2018-01-09 2018-01-16 2018-02-01 8 24 16 66810815fe0a68f5501d8cbe1472779d c7ec40da7b433a48b43ed2c2db0101e8 delivered 2018-01-12 2018-01-13 2018-01-15 2018-01-26 2018-02-07 14 26 12 cc999e83cbddd8f4961651258b551003 7b49c9e88dd17d69f6604c5bab0f1291 delivered 2018-02-23 2018-02-23 2018-02-26 2018-02-28 2018-03-15 5 20 15 cfe5649887c20d8a27d7a9a2302a9d9b 7c9e2de99b4d853ad2849bf211810bcf delivered 2017-12-04 2017-12-04 2017-12-12 2017-12-26 2018-01-04 22 31 9 50a6fb3fc2465d6d820f5a569be4d566 06feba89747b8e9e2a482ca08e3b1c3b delivered 2017-12-28 2017-12-28 2018-01-04 2018-01-15 2018-01-29 18 32 14 7fa9efca67559f2f13c0656e55967397 420b67c85ceff09ec8d61df18ee62125 delivered 2018-01-31 2018-01-31 2018-02-06 2018-02-07 2018-02-16 7 16 9 5b4858f2dcf69731f2

In [0]:
# #joining datasets

order_item_joined_df= orders_df.join(order_items_df,"order_id","inner")
order_item_products_joined_df=order_item_joined_df.join(products_df,"product_id",'inner')
order_item_products_sellers_joined_df=order_item_products_joined_df.join(broadcast(sellers_df),'seller_id','inner')
full_order_df=order_item_products_sellers_joined_df.join(customers_df,'customer_id','inner')
full_order_df=full_order_df.join(broadcast(geolocation_df),full_order_df.customer_zip_code_prefix==geolocation_df.geolocation_zip_code_prefix,'left')
full_order_df=full_order_df.join(broadcast(order_review_df),'order_id','left')
final_df=full_order_df.join(order_payments_df,'order_id','left')


display(final_df)

In [0]:
display(final_df)

In [0]:
final_df=final_df.join(mongodata_spark,"product_category_name","left")
display(final_df)

In [0]:
# making visualization
display(final_df)

In [0]:
final_df.write.mode("overwrite").format("parquet").save("abfss://olist-container@ecommprojstorage.dfs.core.windows.net/silver/")